# Test BCN

## Import data and libs

In [21]:
import pandas as pd
import folium
import matplotlib.pyplot as plt
import re
import random
from folium.plugins import MarkerCluster
import json
from collections import Counter
import geopandas as gpd
from shapely.geometry import Point, LineString

In [3]:
bus_lines = pd.read_csv(".\data\linies_bus.csv")
acc = pd.read_csv('data\ccidents_causes_gu_bcn.csv')

## ZBE map

In [16]:
# Re-load the file and check all top-level features in the JSON
with open("data/ZBE.json", "r", encoding="utf-8") as f:
    full_data = json.load(f)

# Check how many separate feature collections exist (this could be a list of separate layers)
top_level_type = type(full_data)
entry_types = [type(entry) for entry in full_data]
entry_keys = [entry.keys() for entry in full_data]

#entry_types, entry_keys

# Identify each feature collection by inspecting the "name" field
collection_names = [entry["name"] for entry in full_data]

# Count geometry types in each collection
geometry_type_counts = [
    Counter(feature["geometry"]["type"] for feature in entry["features"])
    for entry in full_data
]

list(zip(collection_names, geometry_type_counts))

# Create the map centered on Barcelona
zbe_map = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# Extract each collection
zbe_intrarondes = full_data[0]["features"]
zbe_local = full_data[1]["features"]
vies_excloses = full_data[2]["features"]

# Plot ZBE polygons (both intrarondes and local)
for feature in zbe_intrarondes + zbe_local:
    coords = feature["geometry"]["coordinates"][0]
    polygon = [(lat, lon) for lon, lat in coords]
    folium.Polygon(
        locations=polygon,
        color="green",
        fill=True,
        fill_color="green",
        fill_opacity=0.2,
        weight=2
    ).add_to(zbe_map)

# Plot Vies Excloses (yellow lines)
for feature in vies_excloses:
    geom_type = feature["geometry"]["type"]
    coords = feature["geometry"]["coordinates"]
    
    if geom_type == "LineString":
        line = [(lat, lon) for lon, lat in coords]
        folium.PolyLine(
            locations=line,
            color="yellow",
            weight=4
        ).add_to(zbe_map)
    
    elif geom_type == "MultiLineString":
        for line_coords in coords:
            line = [(lat, lon) for lon, lat in line_coords]
            folium.PolyLine(
                locations=line,
                color="yellow",
                weight=4
            ).add_to(zbe_map)

zbe_map


## Accidents, bus lines, ZBE map

In [18]:
def random_color():
    return "#{:06x}".format(random.randint(0, 0xFFFFFF))

# Initialize the map
m_lines = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# Loop through each MULTILINESTRING in your DataFrame
for line in bus_lines['GEOMETRY']:
    # Extract coordinates
    pattern = re.findall(r"[-+]?[0-9]*\.?[0-9]+", line)
    coords = list(map(float, pattern))
    points = [(coords[i+1], coords[i]) for i in range(0, len(coords), 2)]

    if not points:
        continue

    # Generate a unique color for this line
    line_color = random_color()

    # Add the bus line to the map
    folium.PolyLine(points, color='blue', weight=1).add_to(m_lines)

    # Add circle markers at each bus stop
    #for lat, lon in points:
    #    folium.CircleMarker(
    #        location=(lat, lon),
    #        radius=2,
    #        color=line_color,
    #        fill=True,
    #        fill_color=line_color,
    #        fill_opacity=0.9
    #    ).add_to(m_lines)



marker_cluster = MarkerCluster().add_to(m_lines)

for _, row in acc.iterrows():
    folium.CircleMarker(
        location=[row["Latitud_WGS84"], row["Longitud_WGS84"]],
        radius=0.1,
        color="red",
        fill=True,
        fill_color="red",
        fill_opacity=0.9
    ).add_to(marker_cluster)

for feature in zbe_intrarondes + zbe_local:
    coords = feature["geometry"]["coordinates"][0]
    polygon = [(lat, lon) for lon, lat in coords]
    folium.Polygon(
        locations=polygon,
        color="green",
        fill=True,
        fill_color="green",
        fill_opacity=0.2,
        weight=2
    ).add_to(m_lines)

# Plot Vies Excloses (yellow lines)
for feature in vies_excloses:
    geom_type = feature["geometry"]["type"]
    coords = feature["geometry"]["coordinates"]
    
    if geom_type == "LineString":
        line = [(lat, lon) for lon, lat in coords]
        folium.PolyLine(
            locations=line,
            color="yellow",
            weight=4
        ).add_to(m_lines)
    
    elif geom_type == "MultiLineString":
        for line_coords in coords:
            line = [(lat, lon) for lon, lat in line_coords]
            folium.PolyLine(
                locations=line,
                color="yellow",
                weight=4
            ).add_to(m_lines)

# Display the map
m_lines

## Bus line vs Accidents

In [26]:
# Crear GeoDataFrame de accidentes
gdf_acc = gpd.GeoDataFrame(acc, geometry=gpd.points_from_xy(acc["Longitud_WGS84"], acc["Latitud_WGS84"]), crs="EPSG:4326")

# Crear GeoDataFrame de líneas de bus (asumiendo que cada fila es una línea con una lista de puntos)
# Si tienes columnas separadas con lat/lon para cada punto, primero conviértelo a LineString
gdf_bus = gpd.GeoDataFrame(bus_lines, geometry=gpd.GeoSeries.from_wkt(bus_lines["GEOMETRY"]), crs="EPSG:4326")
# Cambiar a un sistema métrico adecuado para Barcelona (UTM zona 31N)
gdf_acc = gdf_acc.to_crs(epsg=25831)
gdf_bus = gdf_bus.to_crs(epsg=25831)
# Buffer de 100 metros
gdf_bus["buffer"] = gdf_bus.geometry.buffer(50)
# Unir todos los buffers en un solo polígono para simplificar
bus_area = gdf_bus["buffer"].unary_union

# Verificar si los accidentes están dentro del área cubierta por líneas de bus
gdf_acc["near_bus"] = gdf_acc.geometry.within(bus_area)

# Ver resultados
num_total = len(gdf_acc)
num_near = gdf_acc["near_bus"].sum()
porcentaje = 100 * num_near / num_total

print(f"{num_near} de {num_total} accidentes ({porcentaje:.2f}%) ocurrieron a menos de 100 metros de una línea de bus.")


C:\Users\Usuario\AppData\Local\Temp\ipykernel_17384\1715279402.py:13: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  bus_area = gdf_bus["buffer"].unary_union


6438 de 7549 accidentes (85.28%) ocurrieron a menos de 100 metros de una línea de bus.


## Otras cosas

In [ ]:
# Cargar datos
bus_stops = pd.read_csv('data/bus_stops.csv')

# Crear mapa centrado en Barcelona
m = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# Colores únicos por distrito
districts = bus_stops['District.Name'].unique()
colors = plt.cm.get_cmap('tab10', len(districts))
district_color_map = {
    district: f"#{int(colors(i)[0]*255):02x}{int(colors(i)[1]*255):02x}{int(colors(i)[2]*255):02x}"
    for i, district in enumerate(districts)
}

# Añadir paradas al mapa, agrupadas por distrito
for district in districts:
    color = district_color_map[district]
    group = folium.FeatureGroup(name=district)

    stops_district = bus_stops[bus_stops['District.Name'] == district]
    for _, row in stops_district.iterrows():
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=4,
            popup=f"{row['Neighborhood.Name']}<br>{row['District.Name']}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7
        ).add_to(group)

    group.add_to(m)

# Añadir control de capas (toggle distritos)
folium.LayerControl(collapsed=False).add_to(m)

# Guardar el mapa
#m.save('mapa_barcelona_featuregroup.html')
m

FileNotFoundError: [Errno 2] No such file or directory: 'data/bus_stops.csv'

In [ ]:
import pandas as pd
import folium
import matplotlib.pyplot as plt

# Cargar datos
bus_stops = pd.read_csv('data/bus_stops.csv')
transports = pd.read_csv('data/transports.csv')

# Crear mapa base
m = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# -----------------------------
# PARADAS DE BUS por distrito
# -----------------------------
districts = bus_stops['District.Name'].unique()
colors = plt.cm.get_cmap('tab10', len(districts))
district_color_map = {
    district: f"#{int(colors(i)[0]*255):02x}{int(colors(i)[1]*255):02x}{int(colors(i)[2]*255):02x}"
    for i, district in enumerate(districts)
}

for district in districts:
    color = district_color_map[district]
    group = folium.FeatureGroup(name=f"🚌 Bus - {district}")

    stops_district = bus_stops[bus_stops['District.Name'] == district]
    for _, row in stops_district.iterrows():
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=4,
            popup=f"{row['Neighborhood.Name']}<br>{row['District.Name']}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7
        ).add_to(group)

    group.add_to(m)

# -----------------------------
# TRANSPORTES por tipo (Underground, Tram, etc.)
# -----------------------------
transport_types = transports['Transport'].dropna().unique()
transport_colors = plt.cm.get_cmap('Set1', len(transport_types))
type_color_map = {
    t: f"#{int(transport_colors(i)[0]*255):02x}{int(transport_colors(i)[1]*255):02x}{int(transport_colors(i)[2]*255):02x}"
    for i, t in enumerate(transport_types)
}

for transport_type in transport_types:
    color = type_color_map[transport_type]
    group = folium.FeatureGroup(name=f"🚉 {transport_type}")

    stops = transports[transports['Transport'] == transport_type]
    for _, row in stops.iterrows():
        if pd.isna(row['Latitude']) or pd.isna(row['Longitude']):
            continue
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=6,
            popup=f"{row['Station']}<br>{row['District.Name'] or ''}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.9
        ).add_to(group)

    group.add_to(m)

# -----------------------------
# Control de capas
# -----------------------------
folium.LayerControl(collapsed=False).add_to(m)

# Guardar
m.save('mapa_barcelona_bus_transportes.html')


/var/folders/dh/_ks73kfn57l67vxm7b5y16qw0000gn/T/ipykernel_39847/3759938902.py:16: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  colors = plt.cm.get_cmap('tab10', len(districts))
/var/folders/dh/_ks73kfn57l67vxm7b5y16qw0000gn/T/ipykernel_39847/3759938902.py:44: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  transport_colors = plt.cm.get_cmap('Set1', len(transport_types))
